# Get data 

In [ ]:
import google.colab
from pathlib import Path

google.colab.drive.mount("/content/drive", force_remount=True)

import zipfile
with zipfile.ZipFile('/content/drive/MyDrive/EyesDataset.zip', 'r') as archive:
    archive.extractall()

Mounted at /content/drive


In [ ]:
import google.colab
from pathlib import Path

google.colab.drive.mount("/content/drive", force_remount=True)

import zipfile
with zipfile.ZipFile('/content/drive/MyDrive/eyes.zip', 'r') as archive:
    archive.extractall()

Mounted at /content/drive


## BLIP

In [ ]:
# install requirements
import sys
if 'google.colab' in sys.modules:
    print('Running in Colab.')
    !pip3 install transformers==4.15.0 timm==0.4.12 fairscale==0.4.4
    !git clone https://github.com/salesforce/BLIP
    %cd BLIP

Running in Colab.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 76.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 377.0/377.0 KB 42.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 235.4/235.4 KB 30.7 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 880.6/880.6 KB 61.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 199.2/199.2 KB 26.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 97.8 MB/s eta 0:00:00
  Created wheel for fairscale: filename=fairscale-0.4.4-py3-none-any.whl size=292864 sha256=03256195129cca78e4ef7224b04f7e8a3175725db74b1f870227cddcb1fad423
  Stored in directory: /r

In [ ]:
from PIL import Image
import requests
import torch
from torchvision import transforms
from torchvision.transforms.functional import InterpolationMode

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

def load_demo_image(img_path,image_size,device):
    #img = '/content/EyesDataset/000000.jpg' 
    raw_image = Image.open(img_path).convert('RGB')   

    w,h = raw_image.size
    display(raw_image)#.resize((w//5,h//5)))
    
    transform = transforms.Compose([
        transforms.Resize((image_size,image_size),interpolation=InterpolationMode.BICUBIC),
        transforms.ToTensor(),
        transforms.Normalize((0.48145466, 0.4578275, 0.40821073), (0.26862954, 0.26130258, 0.27577711))
        ]) 
    image = transform(raw_image).unsqueeze(0).to(device)   
    return image

In [ ]:
# Image-Text Matching
from models.blip_itm import blip_itm

image_size = 384
image = load_demo_image('/content/EyesDataset/000000.jpg', image_size=image_size,device=device)

model_url = 'https://storage.googleapis.com/sfr-vision-language-research/BLIP/models/model_base_retrieval_coco.pth'
    
model = blip_itm(pretrained=model_url, image_size=image_size, vit='base')
model.eval()
model = model.to(device=device)

caption = 'closed eye'

print('text: %s' %caption)

itm_output = model(image,caption,match_head='itm')
itm_score = torch.nn.functional.softmax(itm_output,dim=1)[:,1]
print('The image and text is matched with a probability of %.4f'%itm_score)

itc_score = model(image,caption,match_head='itc')
print('The image feature and text feature has a cosine similarity of %.4f'%itc_score)
print("______________________________")

itm_output = model(image,'open eye',match_head='itm')
itm_score = torch.nn.functional.softmax(itm_output,dim=1)[:,1]
print('The image and text is matched with a probability of %.4f'%itm_score)

itc_score = model(image,caption,match_head='itc')
print('The image feature and text feature has a cosine similarity of %.4f'%itc_score)

load checkpoint from https://storage.googleapis.com/sfr-vision-language-research/BLIP/models/model_base_retrieval_coco.pth
text: closed eye
The image and text is matched with a probability of 0.4223
The image feature and text feature has a cosine similarity of 0.3123
______________________________
The image and text is matched with a probability of 0.5750
The image feature and text feature has a cosine similarity of 0.3123


In [ ]:
! mkdir '/content/closed'

In [ ]:
! mkdir '/content/open'

In [ ]:
# for all images
import os 

def get_probs(image, filename):
  caption = 'closed eye '

  #print('text: %s' %caption)

  itm_output = model(image,caption,match_head='itm')
  itm_score_closed = torch.nn.functional.softmax(itm_output,dim=1)[:,1]
  #print('The image and text is matched with a probability of %.4f'%itm_score)

  itc_score = model(image,caption,match_head='itc')
  #print('The image feature and text feature has a cosine similarity of %.4f'%itc_score)
  #print("______________________________")

  itm_output_opend = model(image,'open eye or pupil',match_head='itm')
  itm_output_opend = torch.nn.functional.softmax(itm_output_opend,dim=1)[:,1]
  #print('The image and text is matched with a probability of %.4f'%itm_score)

  itc_score = model(image,caption,match_head='itc')
  #print('The image feature and text feature has a cosine similarity of %.4f'%itc_score)
  if itm_output_opend>itm_score_closed:
    print("OPEN", itm_output_opend)
    
    image.save('/content/open/'+filename)
  else:
    print("CLOSED", itm_score_closed)
    image.save('/content/closed/'+filename)
  print(itm_output_opend-itm_score_closed)
  print("____________END__________________")


for filename in os.listdir('/content/EyesDataset'):
  #image = Image.open('/content/EyesDataset/'+filename) 
  image = load_demo_image(img_path='/content/EyesDataset/'+filename ,image_size=image_size,device=device)
  get_probs(image, filename)

CLOSED tensor([0.2889], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([-0.1532], device='cuda:0', grad_fn=<SubBackward0>)
____________END__________________


CLOSED tensor([0.0427], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([-0.0356], device='cuda:0', grad_fn=<SubBackward0>)
____________END__________________


OPEN tensor([0.2489], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([0.0703], device='cuda:0', grad_fn=<SubBackward0>)
____________END__________________


CLOSED tensor([0.2789], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([-0.1233], device='cuda:0', grad_fn=<SubBackward0>)
____________END__________________


CLOSED tensor([0.1278], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([-0.0619], device='cuda:0', grad_fn=<SubBackward0>)
____________END__________________


...

CLOSED tensor([0.1484], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([-0.0666], device='cuda:0', grad_fn=<SubBackward0>)
____________END__________________


CLOSED tensor([0.1465], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([-0.0089], device='cuda:0', grad_fn=<SubBackward0>)
____________END__________________


CLOSED tensor([0.2002], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([-0.0211], device='cuda:0', grad_fn=<SubBackward0>)
____________END__________________


CLOSED tensor([0.1500], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([-0.0572], device='cuda:0', grad_fn=<SubBackward0>)
____________END__________________


OPEN tensor([0.8635], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([0.4806], device='cuda:0', grad_fn=<SubBackward0>)
____________END__________________


In [ ]:
! zip -r closed.zip '/content/closed'

  adding: content/closed/ (stored 0%)
  adding: content/closed/003715.jpg (stored 0%)
  adding: content/closed/002894.jpg (stored 0%)
  adding: content/closed/003084.jpg (stored 0%)
  adding: content/closed/000913.jpg (stored 0%)
  adding: content/closed/003667.jpg (stored 0%)
  adding: content/closed/001894.jpg (stored 0%)
  adding: content/closed/000927.jpg (stored 0%)
  adding: content/closed/000022.jpg (stored 0%)
  adding: content/closed/003995.jpg (deflated 1%)
  adding: content/closed/003571.jpg (stored 0%)
  adding: content/closed/001347.jpg (stored 0%)
  adding: content/closed/000591.jpg (stored 0%)
  adding: content/closed/000590.jpg (stored 0%)
  adding: content/closed/001984.jpg (deflated 0%)
  adding: content/closed/003436.jpg (stored 0%)
  adding: content/closed/003343.jpg (stored 0%)
  adding: content/closed/003966.jpg (stored 0%)
  adding: content/closed/003914.jpg (stored 0%)
  adding: content/closed/003089.jpg (stored 0%)
  adding: content/closed/003055.jpg (stored 0%

In [ ]:
! zip -r open.zip '/content/open'

  adding: content/open/ (stored 0%)
  adding: content/open/002437.jpg (stored 0%)
  adding: content/open/001057.jpg (stored 0%)
  adding: content/open/003540.jpg (stored 0%)
  adding: content/open/001234.jpg (stored 0%)
  adding: content/open/002928.jpg (stored 0%)
  adding: content/open/003982.jpg (stored 0%)
  adding: content/open/003035.jpg (stored 0%)
  adding: content/open/002189.jpg (stored 0%)
  adding: content/open/000322.jpg (stored 0%)
  adding: content/open/001080.jpg (stored 0%)
  adding: content/open/003430.jpg (stored 0%)
  adding: content/open/003716.jpg (stored 0%)
  adding: content/open/002939.jpg (stored 0%)
  adding: content/open/001233.jpg (stored 0%)
  adding: content/open/003620.jpg (stored 0%)
  adding: content/open/003661.jpg (stored 0%)
  adding: content/open/000364.jpg (stored 0%)
  adding: content/open/003163.jpg (stored 0%)
  adding: content/open/001617.jpg (stored 0%)
  adding: content/open/000073.jpg (stored 0%)
  adding: content/open/001886.jpg (stored 0%